In [1]:
from pony import orm

In [2]:
db = orm.Database()

# Définitions

In [3]:
class Enseignant(db.Entity):
    e_mail_ens = orm.PrimaryKey(str)
    nom = orm.Required(str)
    prénom = orm.Required(str)
    tel = orm.Optional(str)
    responsabilités = orm.Set('UE')
    séances = orm.Set('Séance')

In [4]:
class UE(db.Entity):
    code_UE = orm.PrimaryKey(str)
    intitulé = orm.Required(str)
    semestre = orm.Required(int)
    crédit = orm.Optional(int)
    responsable = orm.Required(Enseignant)
    séances = orm.Set('Séance')

In [5]:
class Séance(db.Entity):
    id_séance = orm.PrimaryKey(int, auto=True)
    type = orm.Required(str)
    salle = orm.Required(str)
    date = orm.Required(str)
    heure = orm.Required(str)
    enseignant = orm.Required(Enseignant)
    matière = orm.Required(UE)

# Affichage

In [6]:
orm.show(Séance)

class Séance(Entity):
    id_séance = PrimaryKey(int, auto=True)
    type = Required(str)
    salle = Required(str)
    date = Required(str)
    heure = Required(str)
    enseignant = Required(Enseignant)
    matière = Required(UE)


# Association à un gestionnaire de BD

In [7]:
orm.set_sql_debug(True)

In [8]:
db.bind(provider='sqlite', filename=':memory:')

GET NEW CONNECTION
RELEASE CONNECTION


In [9]:
db.generate_mapping(create_tables=True)

GET CONNECTION FROM THE LOCAL POOL
PRAGMA foreign_keys = false
BEGIN IMMEDIATE TRANSACTION
CREATE TABLE "Enseignant" (
  "e_mail_ens" TEXT NOT NULL PRIMARY KEY,
  "nom" TEXT NOT NULL,
  "prénom" TEXT NOT NULL,
  "tel" TEXT NOT NULL
)

CREATE TABLE "UE" (
  "code_UE" TEXT NOT NULL PRIMARY KEY,
  "intitulé" TEXT NOT NULL,
  "semestre" INTEGER NOT NULL,
  "crédit" INTEGER,
  "responsable" TEXT NOT NULL REFERENCES "Enseignant" ("e_mail_ens")
)

CREATE INDEX "idx_ue__responsable" ON "UE" ("responsable")

CREATE TABLE "Séance" (
  "id_séance" INTEGER PRIMARY KEY AUTOINCREMENT,
  "type" TEXT NOT NULL,
  "salle" TEXT NOT NULL,
  "date" TEXT NOT NULL,
  "heure" TEXT NOT NULL,
  "enseignant" TEXT NOT NULL REFERENCES "Enseignant" ("e_mail_ens"),
  "matière" TEXT NOT NULL REFERENCES "UE" ("code_UE")
)

CREATE INDEX "idx_séance__enseignant" ON "Séance" ("enseignant")

CREATE INDEX "idx_séance__matière" ON "Séance" ("matière")

SELECT "Enseignant"."e_mail_ens", "Enseignant"."nom", "Enseignant"."prén

# Insertion de données

In [12]:
#paul = Enseignant(e_mail_ens = "ppoitevin@ec-m.fr", nom = "Poitevin", prénom = "Paul")
#orm.commit()
paul = Enseignant.get(e_mail_ens = "ppoitevin@ec-m.fr")

In [13]:
martin = Enseignant(e_mail_ens = "mmollo@ec-m.fr", nom = "Mollo", prénom = "Martin")
orm.commit()
#martin = Enseignant.get(e_mail_ens = "mmollo@ec-m.fr")

BEGIN IMMEDIATE TRANSACTION
INSERT INTO "Enseignant" ("e_mail_ens", "nom", "prénom", "tel") VALUES (?, ?, ?, ?)
['mmollo@ec-m.fr', 'Mollo', 'Martin', '']

COMMIT


In [14]:
info = UE(code_UE = 'INF_1', intitulé = 'Informatique', semestre = 5, responsable = paul )
orm.commit()
#info = UE.get(code_UE = 'INF_1')

BEGIN IMMEDIATE TRANSACTION
INSERT INTO "UE" ("code_UE", "intitulé", "semestre", "responsable") VALUES (?, ?, ?, ?)
['INF_1', 'Informatique', 5, 'ppoitevin@ec-m.fr']

COMMIT


In [15]:
s1 = Séance(type = 'CM', salle = 'Amphi 2', date = '2018-09-22', heure = '8:00', enseignant = paul, matière = info)
s2 = Séance(type = 'TD', salle = '222', date = '2018-09-22', heure = '10:15', enseignant = martin, matière = info)
orm.commit()

BEGIN IMMEDIATE TRANSACTION
INSERT INTO "Séance" ("type", "salle", "date", "heure", "enseignant", "matière") VALUES (?, ?, ?, ?, ?, ?)
['CM', 'Amphi 2', '2018-09-22', '8:00', 'ppoitevin@ec-m.fr', 'INF_1']

INSERT INTO "Séance" ("type", "salle", "date", "heure", "enseignant", "matière") VALUES (?, ?, ?, ?, ?, ?)
['TD', '222', '2018-09-22', '10:15', 'mmollo@ec-m.fr', 'INF_1']

COMMIT


# Affichage

In [16]:
print(paul)

Enseignant['ppoitevin@ec-m.fr']


In [17]:
print(paul.prénom, paul.nom)

Paul Poitevin


In [18]:
print(info)

UE['INF_1']


In [19]:
print(info.intitulé)

Informatique


In [21]:
enseignants = Enseignant.select()
enseignants.show()

e_mail_ens       |nom     |prénom|tel
-----------------+--------+------+---
ppoitevin@ec-m.fr|Poitevin|Paul  |   
mmollo@ec-m.fr   |Mollo   |Martin|   


In [22]:
paul.séances.select()[:]

SELECT "s"."id_séance", "s"."type", "s"."salle", "s"."date", "s"."heure", "s"."enseignant", "s"."matière"
FROM "Séance" "s"
WHERE "s"."enseignant" = ?
['ppoitevin@ec-m.fr']



[Séance[1]]

In [23]:
paul.séances.select().show()

id_séance|type|salle  |date      |heure|enseignant                  |matière    
---------+----+-------+----------+-----+----------------------------+-----------
1        |CM  |Amphi 2|2018-09-22|8:00 |Enseignant['ppoitevin@ec-...|UE['INF_1']


In [24]:
paul.responsabilités.select().show()

SELECT "ue"."code_UE", "ue"."intitulé", "ue"."semestre", "ue"."crédit", "ue"."responsable"
FROM "UE" "ue"
WHERE "ue"."responsable" = ?
['ppoitevin@ec-m.fr']

code_UE|intitulé    |semestre|crédit|responsable                    
-------+------------+--------+------+-------------------------------
INF_1  |Informatique|5       |None  |Enseignant['ppoitevin@ec-m.fr']


# Fonctions avec décorateur

In [25]:
@orm.db_session
def affiche_enseigant(e_mail_ens):
    e = Enseignant[e_mail_ens]
    print('Nom:', e.nom)
    print('Prénom:', e.prénom)
    print('Téléphone:', e.tel)
    print('Responsabilités :', e.responsabilités) 
    print('Séances :', e.séances)
    # database session cache will be cleared automatically
    # database connection will be returned to the pool

In [26]:
affiche_enseigant("ppoitevin@ec-m.fr")

Nom: Poitevin
Prénom: Paul
Téléphone: 
Responsabilités : UESet([UE['INF_1']])
Séances : SéanceSet([Séance[1]])
COMMIT
RELEASE CONNECTION


In [27]:
@orm.db_session
def ajoute_séance(e_mail_ens, code_UE, salle, date, heure, type):
    Séance(salle = salle, date = date, heure = heure, type = type, 
           enseignant = Enseignant[e_mail_ens], 
           matière = UE[code_UE])
    # commit() will be done automatically
    # database session cache will be cleared automatically
    # database connection will be returned to the pool

In [28]:
ajoute_séance("ppoitevin@ec-m.fr", "INF_1", "222", "2018-09-22", "13:30", "TD")

GET CONNECTION FROM THE LOCAL POOL
SWITCH TO AUTOCOMMIT MODE
SELECT "e_mail_ens", "nom", "prénom", "tel"
FROM "Enseignant"
WHERE "e_mail_ens" = ?
['ppoitevin@ec-m.fr']

SELECT "code_UE", "intitulé", "semestre", "crédit", "responsable"
FROM "UE"
WHERE "code_UE" = ?
['INF_1']

BEGIN IMMEDIATE TRANSACTION
INSERT INTO "Séance" ("type", "salle", "date", "heure", "enseignant", "matière") VALUES (?, ?, ?, ?, ?, ?)
['TD', '222', '2018-09-22', '13:30', 'ppoitevin@ec-m.fr', 'INF_1']

COMMIT
RELEASE CONNECTION


# Accès en écriture

In [29]:
with orm.db_session:
    Séance[3].salle = '224'
    # commit() will be done automatically
    # database session cache will be cleared automatically
    # database connection will be returned to the pool

GET CONNECTION FROM THE LOCAL POOL
SWITCH TO AUTOCOMMIT MODE
SELECT "id_séance", "type", "salle", "date", "heure", "enseignant", "matière"
FROM "Séance"
WHERE "id_séance" = ?
[3]

BEGIN IMMEDIATE TRANSACTION
UPDATE "Séance"
SET "salle" = ?
WHERE "id_séance" = ?
['224', 3]

COMMIT
RELEASE CONNECTION


In [30]:
Séance[3].heure = '15:45'
orm.commit()

GET CONNECTION FROM THE LOCAL POOL
SWITCH TO AUTOCOMMIT MODE
SELECT "id_séance", "type", "salle", "date", "heure", "enseignant", "matière"
FROM "Séance"
WHERE "id_séance" = ?
[3]

BEGIN IMMEDIATE TRANSACTION
UPDATE "Séance"
SET "heure" = ?
WHERE "id_séance" = ?
['15:45', 3]

COMMIT


In [31]:
Séance.select().show()

BEGIN IMMEDIATE TRANSACTION
SELECT "s"."id_séance", "s"."type", "s"."salle", "s"."date", "s"."heure", "s"."enseignant", "s"."matière"
FROM "Séance" "s"

id_séance|type|salle  |date      |heure|enseignant                  |matière    
---------+----+-------+----------+-----+----------------------------+-----------
1        |CM  |Amphi 2|2018-09-22|8:00 |Enseignant['ppoitevin@ec-...|UE['INF_1']
2        |TD  |222    |2018-09-22|10:15|Enseignant['mmollo@ec-m.fr']|UE['INF_1']
3        |TD  |224    |2018-09-22|15:45|Enseignant['ppoitevin@ec-...|UE['INF_1']


# Requête (sélection)

In [32]:
s = orm.select(s for s in Séance if s.type == 'TD')
s.show()

SELECT "s"."id_séance", "s"."type", "s"."salle", "s"."date", "s"."heure", "s"."enseignant", "s"."matière"
FROM "Séance" "s"
WHERE "s"."type" = 'TD'

id_séance|type|salle|date      |heure|enseignant                    |matière    
---------+----+-----+----------+-----+------------------------------+-----------
2        |TD  |222  |2018-09-22|10:15|Enseignant['mmollo@ec-m.fr']  |UE['INF_1']
3        |TD  |224  |2018-09-22|15:45|Enseignant['ppoitevin@ec-m....|UE['INF_1']


In [38]:
s = orm.select(s for s in Séance if (s.enseignant == paul and s.type == 'TD'))
s.show()

SELECT "s"."id_séance", "s"."type", "s"."salle", "s"."date", "s"."heure", "s"."enseignant", "s"."matière"
FROM "Séance" "s"
WHERE "s"."enseignant" = ?
  AND "s"."type" = 'TD'
['ppoitevin@ec-m.fr']

id_séance|type|salle|date      |heure|enseignant                    |matière    
---------+----+-----+----------+-----+------------------------------+-----------
3        |TD  |224  |2018-09-22|15:45|Enseignant['ppoitevin@ec-m....|UE['INF_1']


# BUG!!:

In [34]:
orm.show(paul)

instance of Enseignant


AttributeError: 'list' object has no attribute '_translator'